Per prima cosa installiamo i pacchetti richiesti

In [ ]:
!pip install -r requirements.txt

Qui l'utente inserisce l'identificatore, che può essere un gene o un accession number uniprot (https://www.uniprot.org/help/accession_numbers)

In [19]:
identificatore = "ALS2, FBN1, BRCA1, ACE2"

Nei prossimi due blocchi effettuiamo un check con una stringa regex per controllare se l'utente ha inserito un accession number uniprot o qualcos'altro.

Se ha inserito un'altra cosa, forse è un gene, quindi proviamo a usare il tool di ID mapping di uniprot tramite la API di uniprot (https://www.uniprot.org/help/id_mapping)

Usiamo il metodo post di requests per inviare la richiesta di ID mapping, poi controlliamo ogni 5s se il lavoro è terminato (essendo un solo id dovrebbe terminare istantaneamente) e troviamo l'accession number uniprot a partire dal gene

In [20]:
import re
import requests
import time

def uniprot_check(identifier):
    regex = "[OPQ][0-9][A-Z0-9]{3}[0-9]|[A-NR-Z][0-9]([A-Z][A-Z0-9]{2}[0-9]){1,2}"
    if re.fullmatch(regex, identifier):
        return True
    else:
        return False

def submit_id_mapping(identifier):
    """
    Questa funzione manda una richiesta al tool ID mapping di uniprot

    Accetta l'id inserito dall'utente in input
    Restituisce un'eccezione o un jobid
    """
    r = None
    url = "https://rest.uniprot.org/idmapping/run"
    data={
        "from": "GeneCards", 
        "to": "UniProtKB", 
        "ids": identifier
        }
    try:
        r = requests.post(url, data)
        return r.json().get("jobId")
    except:
        return Exception

def to_uniprot(jobid):
    """
    Questa funzione controlla periodicamente lo stato del lavoro il cui id
    è fornito come argomento.

    Accetta l'id inserito dall'utente in input
    Restituisce un'eccezione o un jobid
    """
    url = f"https://rest.uniprot.org/idmapping/status/{jobid}"
    while True:
        r = requests.get(url)
        j = r.json()
        if 'jobStatus' in j:
                if j.get("jobStatus") in ("NEW", "RUNNING"):
                        print(f'stato del lavoro: {j.get("jobStatus")}')
                        print(f"Riprovo tra 5s")
                        time.sleep(5)
        else:
            if j.get('results') != []:
                return j.get('results')[0].get('to').get('primaryAccession')
            else:
                return False


In [21]:
print(f'ID inserito: {identificatore}')
if ',' in identificatore:
    id = str.split(identificatore, sep=',')[0]
    print(f'\nAttenzione: è stato rilevato un separatore (",").\nSe hai inserito più identificatori, verrà considerato solo il primo ({id}).\n')
else:
    id = identificatore
if uniprot_check(id):
    print(f"L'ID {id} è un Accession number di UniProt\n ")
else:
    print(f"L'ID inserito non è un Accession Number di Uniprot.\nForse è un gene, provo a convertirlo in Accession Number.\n")
    jobid = submit_id_mapping(id)
    if jobid == Exception:
        print("Errore durante l'invio della richiesta")
    else:
        print(f'Richiesta di mapping inviata correttamente\nID richiesta: {jobid}\nURL richiesta: https://rest.uniprot.org/idmapping/status/{jobid}')
        uniprot_id = to_uniprot(jobid)
        if uniprot_id:
            print(f'Accession number: {uniprot_id}')
        else:
            print(f'Nessun gene trovato con il nome {id}')

ID inserito: ALS2, FBN1, BRCA1, ACE2

Attenzione: è stato rilevato un separatore (",").
Se hai inserito più identificatori, verrà considerato solo il primo (ALS2).

L'ID inserito non è un Accession Number di Uniprot.
Forse è un gene, provo a convertirlo in Accession Number.

Richiesta di mapping inviata correttamente
ID richiesta: fmOT0JwkJk
URL richiesta: https://rest.uniprot.org/idmapping/status/fmOT0JwkJk
stato del lavoro: RUNNING
Riprovo tra 5s
Accession number: Q96Q42


Adesso dobbiamo accedere al file pdb tramite la API del database di alphafold.(https://alphafold.ebi.ac.uk/api-docs)

Per prima cosa mandiamo una richiesta a https://alphafold.com/api/prediction/ seguito dall'identificatore uniprot. Convertiamo la risposta che otteniamo in json e andiamo alla chiave pdbUrl che contiene il file pdb.

Mandiamo un'altra richiesta all'url del file pdb e scriviamo il testo che riceviamo in un file .pdb

Dopo aver eseguito la funzione, usiamo with con l'attributo 'r' per mostrare il file pdb su schermo

In [22]:
import requests

def get_af_pdb(uniprotid):
    url = f"https://alphafold.com/api/prediction/{uniprotid}"
    try:
        response = requests.get(url)
        pdburl = response.json()[0].get('pdbUrl')
        response = requests.get(pdburl)
        with open('proteina.pdb', 'w') as f:
            f.write(response.text)  
        pdb_file = 'proteina.pdb'
        return pdb_file
    except:
        return Exception
    
print(uniprot_id)
pdb_file = get_af_pdb(uniprot_id)

with open(pdb_file, 'r') as f:
    print(f.read())

Q96Q42
HEADER                                            01-JUN-22                     
TITLE     ALPHAFOLD MONOMER V2.0 PREDICTION FOR ALSIN (Q96Q42)                  
COMPND    MOL_ID: 1;                                                            
COMPND   2 MOLECULE: ALSIN;                                                     
COMPND   3 CHAIN: A                                                             
SOURCE    MOL_ID: 1;                                                            
SOURCE   2 ORGANISM_SCIENTIFIC: HOMO SAPIENS;                                   
SOURCE   3 ORGANISM_TAXID: 9606                                                 
REMARK   1                                                                      
REMARK   1 REFERENCE 1                                                          
REMARK   1  AUTH   JOHN JUMPER, RICHARD EVANS, ALEXANDER PRITZEL, TIM GREEN,    
REMARK   1  AUTH 2 MICHAEL FIGURNOV, OLAF RONNEBERGER, KATHRYN TUNYASUVUNAKOOL, 
REMARK   1  AUTH 3 RU

usiamo subito py3dmol https://github.com/avirshup/py3dmol per vedere la proteina
Alcune guide/esempi di py3dmol sono

- https://colab.research.google.com/github/daveminh/Chem456-2022F/blob/main/exercises/02-structural_visualization.ipynb
- https://nbviewer.org/github/3dmol/3Dmol.js/blob/master/py3Dmol/examples.ipynb
- https://william-dawson.github.io/using-py3dmol.html
- https://colab.research.google.com/drive/1T2zR59TXyWRcNxRgOAiqVPJWhep83NV_?usp=sharing

creo una matrice con nome residuo, posizione nella catena e coordinate del carbonio alfa
La posizione della catena si potrebbe pure omettere e usare l'indice, ma la metto lo stesso 

In [167]:
originale=[]
with open(pdb_file, 'r') as f:
    for riga in f:
        if riga.startswith("ATOM"):
            nome_atomo = riga[12:16].strip()
            residuo    = riga[17:20].strip()
            numero_res = riga[22:26].strip()
            x          = float(riga[30:38])
            y          = float(riga[38:46])
            z          = float(riga[46:54])

            if nome_atomo=="CA":
                riga=[residuo, numero_res, x,y,z]
                originale.append(riga)

print(originale)

[['MET', '1', 50.183, 17.561, 37.631], ['ASP', '2', 50.517, 19.247, 34.288], ['SER', '3', 48.003, 19.907, 31.506], ['LYS', '4', 49.646, 17.775, 28.811], ['LYS', '5', 47.202, 18.033, 25.895], ['ARG', '6', 46.226, 14.376, 25.322], ['SER', '7', 46.246, 14.026, 21.557], ['SER', '8', 43.154, 11.824, 20.951], ['THR', '9', 45.335, 9.258, 19.098], ['GLU', '10', 45.978, 6.194, 21.345], ['ALA', '11', 42.91, 3.967, 21.312], ['GLU', '12', 45.044, 0.842, 22.103], ['GLY', '13', 42.696, -1.477, 20.039], ['SER', '14', 43.021, 0.121, 16.51], ['LYS', '15', 46.536, -1.315, 15.682], ['GLU', '16', 45.464, -4.942, 16.357], ['ARG', '17', 42.585, -5.546, 13.821], ['GLY', '18', 42.507, -6.079, 10.014], ['LEU', '19', 46.122, -7.411, 9.748], ['VAL', '20', 46.907, -8.205, 6.077], ['HIS', '21', 48.556, -11.601, 5.424], ['ILE', '22', 49.318, -12.768, 1.834], ['TRP', '23', 50.081, -16.167, 0.272], ['GLN', '24', 51.123, -17.138, -3.259], ['ALA', '25', 48.756, -19.643, -4.947], ['GLY', '26', 50.239, -23.118, -5.73], [

In [168]:
import py3Dmol as p3d

v = p3d.view(query='proteina.pdb')
v.setStyle({"stick": {'color': 'spectrum'}})
v.addSurface(p3d.VDW,{'opacity':0.7,'color':'spectrum'})
# v.addLabel("H41",{'fontOpacity':1},{'resi':'41'})
# v.zoomTo({'resi':'4'})
v.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

A questo punto ci serve la lista delle mutazioni da clinvar.
In questa cella uso il modulo Entrez di Biopython che permette di cercare una query u un database e ottenere una lista di ID che corrispondono a dei record in quel database

In [169]:
from Bio import Entrez

from Bio import Entrez
from urllib.error import HTTPError

def cvsearch(gene):
    # entrez email
    Entrez.email = "italoruttico@gmail.com"

    #variabili
    database = "clinvar"
    max = 1000
    ricerca = gene + '''[gene] AND "mol cons missense"[filter]'''
    print(ricerca)
    
    #cerca
    try :
        handle = Entrez.esearch(db=database, 
                                term=ricerca,
                                retmax=500)
        record = Entrez.read(handle)
        handle.close()
    except HTTPError:
        print('Errore durante la ricerca su ClinVar')
        return None
        
    return record["IdList"]
    
id_list=cvsearch('ALS2')
print(id_list)

ALS2[gene] AND "mol cons missense"[filter]
['3859930', '3859920', '3859910', '3859901', '3859892', '3859881', '3859873', '3859869', '3859858', '3859847', '3859836', '3859828', '3859814', '3781292', '3779423', '3775205', '3765943', '3730952', '3703325', '3702973', '3668681', '3641468', '3571890', '3534106', '3534091', '3534072', '3534062', '3534003', '3389887', '3389300', '3377954', '3376012', '3354489', '3292018', '3292008', '3291997', '3291967', '3257349', '3257077', '3114176', '3114161', '3114144', '3114143', '3114132', '3114113', '3114106', '3114094', '3114066', '3114058', '3009677', '2973077', '2967173', '2831433', '2824945', '2812833', '2808754', '2798611', '2693479', '2690990', '2684239', '2682809', '2662165', '2613274', '2612091', '2610049', '2585228', '2578894', '2574619', '2487443', '2482052', '2443467', '2439008', '2420952', '2418062', '2417559', '2416585', '2333794', '2313026', '2294773', '2290005', '2285685', '2276075', '2269447', '2258536', '2256441', '2219867', '2200927',

Qui invece uso esummary che data un db e una lista di id restituisce un handle che può essere in formato xml o json. Ho scelto il formato json. 

Con json.load lo ho trasformato in dizionario. Le chiavi erano header e result. 

L'header mostra il tipo di eutil utilizzato (esummary) e la versione, quindi ho tenuto result che è un altro dizionario che contiene i risultati.

Poi con json.dump lo ho stampato per mostrare la struttura.

In [170]:
import json

def cvsummary(idlist):
        handle = Entrez.esummary(db="clinvar", id=idlist, retmode="json")    
        record = json.load(handle)
        handle.close()

        print(record.keys())
        print(record['header'])
        data = record.get('result')

        return data

cv_json = cvsummary(id_list)

print(json.dumps(cv_json, indent=4))

dict_keys(['header', 'result'])
{'type': 'esummary', 'version': '0.3'}
{
    "uids": [
        "3859930",
        "3859920",
        "3859910",
        "3859901",
        "3859892",
        "3859881",
        "3859873",
        "3859869",
        "3859858",
        "3859847",
        "3859836",
        "3859828",
        "3859814",
        "3781292",
        "3779423",
        "3775205",
        "3765943",
        "3730952",
        "3703325",
        "3702973",
        "3668681",
        "3641468",
        "3571890",
        "3534106",
        "3534091",
        "3534072",
        "3534062",
        "3534003",
        "3389887",
        "3389300",
        "3377954",
        "3376012",
        "3354489",
        "3292018",
        "3292008",
        "3291997",
        "3291967",
        "3257349",
        "3257077",
        "3114176",
        "3114161",
        "3114144",
        "3114143",
        "3114132",
        "3114113",
        "3114106",
        "3114094",
        "3114066",
 

In [171]:
import re

#pattern che alla fine contenga (p.
pattern = re.compile(r'.*\(p\.[A-Za-z]{3}\d+[A-Za-z]{3}\)$')

tratti = []
varianti = []

for record in cv_json:
    if record != 'uids':
        if pattern.match(cv_json[record].get('title')):
            if cv_json[record].get('germline_classification').get('trait_set') != [] :
                for trait in cv_json[record].get('germline_classification').get('trait_set'):
                        tratto_clinico = cv_json[record].get('germline_classification').get('trait_set')[0].get('trait_name')
                        if tratto_clinico != 'not provided' and tratto_clinico != 'not specified':
                            varianti.append(cv_json[record].get('title'))


mutazioni=varianti
print(mutazioni)


['NM_020919.4(ALS2):c.4244T>C (p.Ile1415Thr)', 'NM_020919.4(ALS2):c.3554A>T (p.Gln1185Leu)', 'NM_020919.4(ALS2):c.646C>G (p.Leu216Val)', 'NM_020919.4(ALS2):c.4583A>G (p.Lys1528Arg)', 'NM_020919.4(ALS2):c.1319C>T (p.Ala440Val)', 'NM_020919.4(ALS2):c.178G>A (p.Gly60Ser)', 'NM_020919.4(ALS2):c.2419G>A (p.Asp807Asn)', 'NM_020919.4(ALS2):c.3831A>C (p.Lys1277Asn)', 'NM_020919.4(ALS2):c.1519G>A (p.Val507Met)', 'NM_020919.4(ALS2):c.344G>T (p.Trp115Leu)', 'NM_020919.4(ALS2):c.1337T>G (p.Leu446Trp)', 'NM_020919.4(ALS2):c.436C>T (p.Pro146Ser)', 'NM_020919.4(ALS2):c.1330G>A (p.Glu444Lys)', 'NM_020919.4(ALS2):c.1382G>A (p.Gly461Glu)', 'NM_020919.4(ALS2):c.529G>T (p.Gly177Cys)', 'NM_020919.4(ALS2):c.1653G>T (p.Leu551Phe)', 'NM_020919.4(ALS2):c.3443C>T (p.Pro1148Leu)', 'NM_020919.4(ALS2):c.145G>A (p.Gly49Arg)', 'NM_020919.4(ALS2):c.2846C>G (p.Ser949Cys)', 'NM_020919.4(ALS2):c.3662A>G (p.Tyr1221Cys)', 'NM_020919.4(ALS2):c.3431C>A (p.Thr1144Lys)', 'NM_020919.4(ALS2):c.1301C>T (p.Ala434Val)', 'NM_020919

ora con re creo 3 liste, una con l'AA WT (il primo), una con le posizioni, e una con l'AA mutato

In [185]:
import re

pattern = re.compile(r"\(p\.([A-Z][a-z]{2})(\d+)([A-Z][a-z]{2})\)")

for i in range(len(mutazioni)):
    #if perché si può usare una sola volta dato che poi si sostituisce la stringa (es. NM_000138.5(FBN1):c.3646G>A (p.Glu1216Lys) con una lista)
    if type(mutazioni[i]) == str:
        match = pattern.search(mutazioni[i])
        if match:
            wt, pos, mut = match.groups()
            mutazioni[i] = [wt.upper(), pos, mut.upper()]

print(mutazioni)
print(len(mutazioni))

[['ILE', '1415', 'THR'], ['GLN', '1185', 'LEU'], ['LEU', '216', 'VAL'], ['LYS', '1528', 'ARG'], ['ALA', '440', 'VAL'], ['GLY', '60', 'SER'], ['ASP', '807', 'ASN'], ['LYS', '1277', 'ASN'], ['VAL', '507', 'MET'], ['TRP', '115', 'LEU'], ['LEU', '446', 'TRP'], ['PRO', '146', 'SER'], ['GLU', '444', 'LYS'], ['GLY', '461', 'GLU'], ['GLY', '177', 'CYS'], ['LEU', '551', 'PHE'], ['PRO', '1148', 'LEU'], ['GLY', '49', 'ARG'], ['SER', '949', 'CYS'], ['TYR', '1221', 'CYS'], ['THR', '1144', 'LYS'], ['ALA', '434', 'VAL'], ['ASP', '284', 'ALA'], ['ASP', '1629', 'GLY'], ['MET', '689', 'LEU'], ['GLU', '1337', 'GLY'], ['GLU', '967', 'ASP'], ['LYS', '1413', 'THR'], ['HIS', '271', 'ARG'], ['HIS', '271', 'ARG'], ['GLU', '1636', 'LYS'], ['SER', '1335', 'ARG'], ['LEU', '1213', 'TRP'], ['ILE', '1152', 'THR'], ['CYS', '1126', 'TYR'], ['CYS', '874', 'SER'], ['ALA', '616', 'VAL'], ['CYS', '552', 'SER'], ['CYS', '552', 'SER'], ['GLU', '359', 'GLN'], ['ARG', '34', 'GLY'], ['VAL', '301', 'ALA'], ['ALA', '519', 'VAL']

adesso tengo solo le mutazioni che esistono sulla struttura della proteina

In [ ]:
mut_verificate=[]
coords_verificate=[]
for m in mutazioni:
    coppia_m=[m[0],m[1]]
    for o in originale:
        coppia_o=[o[0],o[1]]
        if coppia_m==coppia_o:
            coords=[o[2],o[3],o[4]]
            mut_verificate.append([m[0],m[1],m[2]])
            coords_verificate.append(coords)

print(mut_verificate)
M=[mut_verificate, coords_verificate]



[['ILE', '1415', 'THR'], ['GLN', '1185', 'LEU'], ['LEU', '216', 'VAL'], ['LYS', '1528', 'ARG'], ['ALA', '440', 'VAL'], ['GLY', '60', 'SER'], ['ASP', '807', 'ASN'], ['LYS', '1277', 'ASN'], ['VAL', '507', 'MET'], ['TRP', '115', 'LEU'], ['LEU', '446', 'TRP'], ['PRO', '146', 'SER'], ['GLU', '444', 'LYS'], ['GLY', '461', 'GLU'], ['GLY', '177', 'CYS'], ['LEU', '551', 'PHE'], ['PRO', '1148', 'LEU'], ['GLY', '49', 'ARG'], ['SER', '949', 'CYS'], ['TYR', '1221', 'CYS'], ['THR', '1144', 'LYS'], ['ALA', '434', 'VAL'], ['ASP', '284', 'ALA'], ['ASP', '1629', 'GLY'], ['MET', '689', 'LEU'], ['GLU', '1337', 'GLY'], ['GLU', '967', 'ASP'], ['LYS', '1413', 'THR'], ['HIS', '271', 'ARG'], ['HIS', '271', 'ARG'], ['GLU', '1636', 'LYS'], ['SER', '1335', 'ARG'], ['LEU', '1213', 'TRP'], ['ILE', '1152', 'THR'], ['CYS', '1126', 'TYR'], ['CYS', '874', 'SER'], ['ALA', '616', 'VAL'], ['CYS', '552', 'SER'], ['CYS', '552', 'SER'], ['GLU', '359', 'GLN'], ['ARG', '34', 'GLY'], ['VAL', '301', 'ALA'], ['ALA', '519', 'VAL']

Mi sono appena ricordato che le coordinate non servono perché c'è resi

In [206]:
import py3Dmol as p3d

v = p3d.view(query='proteina.pdb')
v.setStyle({"stick": {'color': 'spectrum'}})
v.addSurface(p3d.VDW,{'opacity':0.7,'color':'spectrum'})
for m in mut_verificate:
    v.addLabel(f'{m[0].capitalize()}{m[1]}{m[2].capitalize()}',{'fontOpacity':1},{'resi':f'{m[1]}'})
# v.zoomTo({'resi':'4'})
v.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.